<a href="https://colab.research.google.com/github/harveyrutland/HRI/blob/main/swarmconfig_multiagent.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Demo

 

1.   Red triangle = boat
2.   yellow region = view region
3. blue dot = shark fin





script 2 (underdevelopment)

In [198]:
import numpy as np
import matplotlib.pyplot as plt
import random
import matplotlib.patches as patches
from matplotlib import animation, rc
from IPython.display import HTML
import math
from shapely.geometry import Point
from shapely.geometry.polygon import Polygon
from math import atan2, degrees, radians
from numpy import linalg as LA
from scipy.spatial import distance
import os

def init():
    return ()



def get_angle(point_1, point_2): 
    angle = atan2(point_1[1] - point_2[1], point_1[0] - point_2[0])
    return angle


def adjust_position_perpX(boat,fin,dist): 
  angle = get_angle(boat,fin)
  boatx_delta = 3.25 * math.cos(angle)
  if boatx_delta > 0:
    boatx_delta = 0
  return boatx_delta


def adjust_position_perpY(deltX, angle):
  y_adjustment = math.tan(angle) * deltX
  return y_adjustment







class SetEnv:
  def __init__(self):
    self.rect_startx = random.uniform(2.5, 5)
    rect_starty1 = random.uniform(0, 0.5)
    rect_starty2 = random.uniform(4.5, 5)
    randomy = random.uniform(0,1)
    if randomy == 0:
      self.rect_starty = rect_starty1
    else:
      self.rect_starty = rect_starty2

  def print_boats(self):
        print(self.num)
  
  def clear_frames(self):
    #frame of animation
    ax.clear()
    ax.set_xlim(( 0, 10))
    ax.set_ylim((0,6))
  
  def add_start_box(self):
    #start square 
    ax.add_patch(patches.Rectangle((self.rect_startx, self.rect_starty),2.5,2.5,fill=False))
    return self.rect_startx, self.rect_starty
    #frames
    # p = plt.Polygon(np.c_[x,y], color='white')
    # ax.add_patch(p)






class AddBoats(SetEnv):
   def __init__(self, set_env):
        self.ascending = True
        self.seen_boat1 = False
        self.search_state = True 


        # boat view point and and angle variables 
        self.angle = random.uniform(0, 360)  
        # random angle view point rotation limits are set with -1.5 to 1.5 rad as upper and lower limits self.angle is subtracted to adjust to position of boat 
        self.boat_rotation = self.angle



        # self.rotation = math.radians(self.angle) 
        self.rotation = self.angle
        #sets the correct boat starting position relative to 0 
        self.boat_rotation_offset = 0
        self.perp_offsetdjustment = 0 
        self.dist = 0 
        

        #---- variable to dtermine direction in which shark is travelling ----# 
        self.last_angle = 0
        self.first_angle = 0 


        self.follow_shark_perp = False
        self.direction_check_interval = 0


        #change back to start random
        self.boat1_startx = random.uniform(set_env.rect_startx, set_env.rect_startx+1)
        self.boat1_starty = random.uniform(set_env.rect_starty, set_env.rect_starty+1)

  
   def set_rotation(self, x_fin, y_fin):




   

     if self.search_state == True:
       if self.ascending == True:
         self.rotation += 0.1
         if self.rotation >= (1.5 + self.angle):
           self.ascending = False
        
       if self.ascending == False:
         self.rotation += -0.1
         if self.rotation <= (-1.5 + self.angle):
           self.ascending = True 

     elif self.search_state == False:
        self.rotation = get_angle([x_fin, y_fin], [self.boat1_startx, self.boat1_starty])

     self.xoffset1 = math.cos(self.rotation)*4
     self.yoffset1 = math.sin(self.rotation)*4
     self.xoffsetL = math.cos(self.rotation - 0.5)*4
     self.yoffsetL = math.sin(self.rotation - 0.5)*4
     self.xoffsetR = math.cos(self.rotation + 0.5)*4
     self.yoffsetR = math.sin(self.rotation + 0.5)*4

     

     self.xoffset2 = math.cos(self.boat_rotation + self.perp_offsetdjustment + math.radians(self.boat_rotation_offset))*0.5
     self.yoffset2 = math.sin(self.boat_rotation + self.perp_offsetdjustment + math.radians(self.boat_rotation_offset))*0.5
   



   def follow_shark(self, x_fin, y_fin):
      if self.seen_boat1 == True:
        self.first_angle = get_angle([x_fin, y_fin], [self.boat1_startx, self.boat1_starty])
        # print('first anf' , self.first_angle)
        if abs(degrees(self.first_angle)) > 80:
          self.search_state = False
          8
          
          x = [self.boat1_startx, x_fin[0]]
          y = [self.boat1_starty, y_fin[0]]
          delta_x = abs(self.boat1_startx - x_fin[0])
          delta_y = abs(self.boat1_starty - y_fin[0])
          self.dist = math.sqrt(delta_x**2 + delta_y**2)
    

          
          if self.dist >= 2 and self.follow_shark_perp == False:
            # self.boat_rotation = self.rotation
            # self.boat1_startx, self.boat1_starty = move_to_shark(self.boat1_startx, self.boat1_starty, x_fin[0], y_fin[0])
            self.boat_rotation = self.rotation
            boat_path = np.linspace([self.boat1_startx, self.boat1_starty],[x_fin[0], y_fin[0]], 5)
            self.boat1_startx, self.boat1_starty = (boat_path[1][0], boat_path[1][1])
          
          if self.dist < 2 and self.follow_shark_perp == False:
            # write_to_log('Distance between boat and shark is:', dist)
            self.direction = 0
            self.direction_check_interval +=1
            
            if self.first_angle > self.last_angle:
              self.direction = 0
            elif self.first_angle < self.last_angle:
              self.direction = 1
            self.last_angle = self.first_angle 
            if self.direction_check_interval == 5:
              angle_changes = [90, -90]
              self.boat_rotation_offset = angle_changes[self.direction]
       
              self.follow_shark_perp = True
              # write_to_log('following perpendicular to shark')
              self.direction_check_interval = 0
     
      else:
        search_state = True 
        

      #follow shark perpendicular  
      if self.follow_shark_perp == True:

        self.direction_check_interval += 1
        boat_deltaY = 0
        if self.direction_check_interval == 2:

          self.boat_deltaX = adjust_position_perpX([self.boat1_startx, self.boat1_starty],[x_fin, y_fin], self.dist)
          
          
          init_angle = self.boat_rotation + self.perp_offsetdjustment + math.radians(self.boat_rotation_offset)
          radjutsment = adjust_position_perpY(self.boat_deltaX , init_angle)

          # if self.dist < 0.5:
          #   print('within safety threshold limit')
          #   self.perp_offsetdjustment = math.radians(45)
          #   boat_deltaY = self.boat_deltaX * math.tan(radians(-45))
         

          if self.dist < 1.7 :
            # print('less than theshold')
            self.perp_offsetdjustment = math.radians(20)
            boat_deltaY = self.boat_deltaX * math.tan(radians(-20))
          
          if self.dist > 2.5:
            # print('greater than theshold')
            self.perp_offsetdjustment = math.radians(-20)
            boat_deltaY = self.boat_deltaX * math.tan(radians(20))
            
          elif self.dist <= 2.5 and self.dist >= 1.7:
            self.perp_offsetdjustment = 0 

          self.boat1_startx = self.boat1_startx + abs(self.boat_deltaX)
          self.boat1_starty = self.boat1_starty + boat_deltaY - radjutsment
          self.direction_check_interval = 0
      

  
      
    
        
   
  
   def plot_boats(self, x_fin, y_fin):
      ax.plot([self.boat1_startx, self.boat1_startx + self.xoffsetL], [self.boat1_starty, self.boat1_starty + self.yoffsetL] , 'bo', linestyle="--", markevery=[0], markersize=2)
      ax.plot([self.boat1_startx, self.boat1_startx + self.xoffsetR], [self.boat1_starty, self.boat1_starty + self.yoffsetR] , 'bo', linestyle="--", markevery=[0], markersize=2)
      x = np.append([self.boat1_startx, self.boat1_startx + self.xoffsetL], [self.boat1_startx, self.boat1_startx + self.xoffsetR][::-1])
      y = np.append([self.boat1_starty, self.boat1_starty + self.yoffsetL],[self.boat1_starty, self.boat1_starty + self.yoffsetR] [::-1])



      # p = plt.Polygon(np.c_[x,y], color="lemonchiffon")
      # ax.add_patch(p)
      view_region = Polygon([(self.boat1_startx, self.boat1_starty), (self.boat1_startx + self.xoffsetL, self.boat1_starty + self.yoffsetL),(self.boat1_startx + self.xoffsetR, self.boat1_starty + self.yoffsetR)])
      point = Point(x_fin, y_fin)

      self.seen_boat1 = view_region.contains(point)
      # ax.plot([self.boat1_startx, self.boat1_startx + self.xoffset1],
      #         [self.boat1_starty, self.boat1_starty + self.yoffset1] , 
      #         'ro', linestyle="--", 
      #         markevery=[0],marker=(3, 0, (35 + math.degrees(self.boat_rotation) + self.boat_rotation_offset + self.perp_offsetdjustment)),  markersize=20)
      

      ax.plot([self.boat1_startx, self.boat1_startx + self.xoffset2], [self.boat1_starty, self.boat1_starty + self.yoffset2] , 'go', linestyle="-", markevery=[0], markersize=2, linewidth=5)


      ax.plot([self.boat1_startx, self.boat1_startx + self.xoffset1],
              [self.boat1_starty, self.boat1_starty + self.yoffset1] , 
              'ro', linestyle="--", 
              markevery=[0],marker=(3, 0, (35 + math.degrees(self.boat_rotation + self.perp_offsetdjustment)+ self.boat_rotation_offset)),  markersize=20)
      
      
      return self.seen_boat1









class AddShark:
  #shark
   def __init__(self):
    self.count = 0
    start = [0],[random.uniform(1, 3)]
    end = [10],[random.uniform(1, 3)]
    N = 211
    self.frame_count = 100
    self.targetpath = np.linspace(start, end, N)
    count_interval = (N-11)/100
    self.count_interval = int(count_interval)
    
  
   def plot_shark(self, count=0, angle=0):
     x_tail = self.targetpath[count][0]
     y_tail = self.targetpath[count][1]
     x_fin = self.targetpath[count+5][0]
     y_fin = self.targetpath[count+5][1]
     x_mouth = self.targetpath[count+10][0]
     y_mouth = self.targetpath[count+10][1]

     tail = [x_tail, x_fin], [y_tail, y_fin]
     fin = x_fin, y_fin
     mouth = [x_fin, x_mouth], [y_fin, y_mouth]
     ax.plot([x_fin, x_mouth], [y_fin, y_mouth], 'bo', linestyle="--", marker=(3, 0, angle))
     ax.plot(x_fin, y_fin, 'bo')
     ax.plot([x_tail, x_fin], [y_tail, y_fin], 'bo', linestyle="--", marker=(3, 0, angle))
     return x_fin, y_fin






# First set up the figure, the axis, and the plot element we want to animate
fig, ax = plt.subplots()
fig.set_size_inches(10, 6)
plt.close()


setEnv=SetEnv()
addShark=AddShark()
Boat1 = AddBoats(setEnv)
Boat2 = AddBoats(setEnv)
Boat3 = AddBoats(setEnv)
Boat4 = AddBoats(setEnv)
Boat5 = AddBoats(setEnv)
setEnv.clear_frames()
setEnv.add_start_box()






def animate(i):
  setEnv.clear_frames()
  setEnv.add_start_box()
  x_fin, y_fin =addShark.plot_shark(addShark.count, 0)
  addShark.count += addShark.count_interval
  
  Boat1.set_rotation(x_fin, y_fin)
  Boat1.plot_boats(x_fin, y_fin)
  Boat1.follow_shark(x_fin, y_fin)

  Boat2.set_rotation(x_fin, y_fin)
  Boat2.follow_shark(x_fin, y_fin)
  Boat2.plot_boats(x_fin, y_fin)

  Boat3.set_rotation(x_fin, y_fin)
  Boat3.follow_shark(x_fin, y_fin)
  Boat3.plot_boats(x_fin, y_fin)
  
  Boat4.set_rotation(x_fin, y_fin)
  Boat4.plot_boats(x_fin, y_fin)
  Boat4.follow_shark(x_fin, y_fin)

  Boat5.set_rotation(x_fin, y_fin)
  Boat5.plot_boats(x_fin, y_fin)
  Boat5.follow_shark(x_fin, y_fin)
 
 



  

        
        
       
  return ()


    

anim = animation.FuncAnimation(fig, animate, init_func=init, frames= addShark.frame_count+1, interval=100, blit=True)

# Note: below is the part which makes it work on Colab
rc('animation', html='jshtml')
anim



















    


  
